In [658]:
import pandas as pd
import numpy as np
from sklearn import preprocessing
from sklearn.metrics.pairwise import linear_kernel, cosine_similarity, paired_euclidean_distances
from sklearn.manifold import TSNE
import plotly.graph_objects as go
from plotly.graph_objs import *

df = pd.read_csv('metrics.csv')
df = df.dropna().reset_index().drop(columns='index')
print(df.shape)
df.head()

(19176, 19)


file             author  \
0     project_gutenberg/9999.txt  Sarah H. Bradford   
1  project_gutenberg/56195-0.txt       Kenneth Ward   
2    project_gutenberg/51187.txt        John Wilson   
3    project_gutenberg/51185.txt  Daniel F. Galouye   
4     project_gutenberg/9997.txt    Francis Parkman   

                                             title  year      sttr  \
0                 Harriet, The Moses of Her People  1822  0.624214   
1          The Boy Volunteers on the Belgian Front  1941  0.585125   
2          A Visit to the Mammoth Cave of Kentucky  1972  0.620000   
3                           All Jackson's Children  1970  0.627000   
4  France and England in North America, Part Third  2013  0.686821   

   hapax_legomenon      yules_k  function_words  avg_sentence_length_word  \
0         0.452214   528.796852        0.398840                 20.889773   
1         0.415000   378.878385        0.397120                 14.213115   
2         0.444000  1298.919399        0.428477                 27.300300   
3         0.486000  1703.701946        0.324357                  8.565289   
4         0.541750   269.095482        0.372508                 21.562230   

   avg_sentence_length_chars  avg_syllables_per_word  punctuation_sentence  \
0                 111.791794                1.735272              4.017759   
1                  77.207650                1.752356              2.763206   
2                 146.405405                1.720949              4.384384   
3                  49.239669                1.794130              2.674380   
4                 122.567266                1.868661              4.204856   

   shannon_entropy  simpsons_d  average_nps  noun_to_verb  noun_to_adj  \
0        10.845536    0.998584   232.700000      0.640382     0.792910   
1        10.506952    0.997945   232.130435      0.603311     0.811363   
2        10.003001    0.998360   222.800000      0.656081     0.777569   
3         9.511655    0.996898   221.166667      0.586852     0.823569   
4        11.781284    0.998751   241.057143      0.716877     0.837261   

   verb_to_adv  avg_dependency_distance  
0     0.717273                 2.338342  
1     0.718462                 2.134627  
2     0.638938                 2.403897  
3     0.692679                 2.098842  
4     0.751203                 2.331626

## Recommendation System

In [471]:
## standard scaling all style metrics; each will have mean 0 and std 1
metrics = df.iloc[:, 4:].values
scaler = preprocessing.MinMaxScaler()
metrics_scaled = scaler.fit_transform(metrics)
df_scaled = pd.DataFrame(metrics_scaled, columns=df.columns[4:])
df_scaled = pd.concat([df.iloc[:,:4], df_scaled], axis=1)
df_scaled.head()

file             author  \
0     project_gutenberg/9999.txt  Sarah H. Bradford   
1  project_gutenberg/56195-0.txt       Kenneth Ward   
2    project_gutenberg/51187.txt        John Wilson   
3    project_gutenberg/51185.txt  Daniel F. Galouye   
4     project_gutenberg/9997.txt    Francis Parkman   

                                             title  year      sttr  \
0                 Harriet, The Moses of Her People  1822  0.580262   
1          The Boy Volunteers on the Belgian Front  1941  0.536514   
2          A Visit to the Mammoth Cave of Kentucky  1972  0.575546   
3                           All Jackson's Children  1970  0.583380   
4  France and England in North America, Part Third  2013  0.650332   

   hapax_legomenon   yules_k  function_words  avg_sentence_length_word  \
0         0.421767  0.050518        0.784760                  0.255357   
1         0.382376  0.035444        0.781371                  0.164938   
2         0.413072  0.127953        0.843135                  0.342173   
3         0.457528  0.168654        0.638047                  0.088452   
4         0.516539  0.024405        0.732892                  0.264464   

   avg_sentence_length_chars  avg_syllables_per_word  punctuation_sentence  \
0                   0.229973                0.450676              0.074117   
1                   0.150698                0.461159              0.050926   
2                   0.309316                0.441888              0.080895   
3                   0.086589                0.486792              0.049284   
4                   0.254673                0.532525              0.077576   

   shannon_entropy  simpsons_d  average_nps  noun_to_verb  noun_to_adj  \
0         0.708580    0.996930     0.678248      0.404288     0.517212   
1         0.673516    0.995543     0.676566      0.342800     0.560263   
2         0.621327    0.996444     0.649016      0.430328     0.481421   
3         0.570443    0.993273     0.644193      0.315501     0.588741   
4         0.805486    0.997291     0.702925      0.531166     0.620684   

   verb_to_adv  avg_dependency_distance  
0     0.502914                 0.323430  
1     0.505006                 0.247857  
2     0.365188                 0.347749  
3     0.459674                 0.234581  
4     0.562570                 0.320938

In [ ]:
[['sttr', 'hapax_legomenon', 'yules_k', 'function_words', 
  'avg_sentence_length_word', 'avg_sentence_length_chars', 
  'avg_syllables_per_word', 'punctuation_sentence', 
  'shannon_entropy', 'simpsons_d', 'average_nps', 'noun_to_verb', 
  'noun_to_adj', 'verb_to_adv', 'avg_dependency_distance']]

In [716]:
df_scaled_subset = df_scaled[['sttr', 'hapax_legomenon', 'yules_k',
                              'avg_sentence_length_word', 'avg_sentence_length_chars', 
                              'avg_syllables_per_word', 'punctuation_sentence', 'shannon_entropy', 
                              'simpsons_d', 'average_nps', 'noun_to_verb', 'noun_to_adj', 
                              'verb_to_adv','avg_dependency_distance'
                              ]]

In [717]:
## scaled cosine sim
cosine_sim = cosine_similarity(df_scaled_subset, df_scaled_subset)

In [590]:
cosine_sim = cosine_similarity(df_TSNE.iloc[:, 4:], df_TSNE.iloc[:, 4:])

In [718]:
indices = pd.Series(df.index, index=df['title'])

In [719]:
# takes book title as input and outputs most similar books
def get_recommendations(title, cosine_sim=cosine_sim):
    # gets index of book that matches title
    idx = indices[title]

    # gets pairwise similarity scores of all books with that book
    sim_scores = list(enumerate(cosine_sim[idx]))

    # sorts books based on the similarity scores
    sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)

    # gets scores of the 10 most similar movies
    sim_scores = sim_scores[1:11]

    # gets book indices
    book_indices = [i[0] for i in sim_scores]

    # returns top 10 most similar books
    return df[['author', 'title']].iloc[book_indices]

In [721]:
get_recommendations('A Tale of Two Cities')

author                                  title
14545              Eugene Sue  The Mysteries of Paris, Volume 4 of 6
8568      Florence L. Barclay              The Following of the Star
14554              Eugene Sue  The Mysteries of Paris, Volume 1 of 6
10813  E. D. E. N. Southworth                  The Haunted Homestead
16790          R M Ballantyne                        Under the Waves
16982         R.M. Ballantyne                    Fighting the Flames
9843         C. N. Williamson        Lord Loveland Discovers America
5042     Elizabeth C. Gaskell                 Round the Sofa; vol. 2
14197         John Galsworthy  The Forsyte Saga, The Man Of Property
7014              Leo Tolstoy         The Invaders and other Stories

In [650]:
df[df.author == 'Henry James']

file       author  \
1548     project_gutenberg/898-0.txt  Henry James   
1727     project_gutenberg/55078.txt  Henry James   
1801   project_gutenberg/60040-0.txt  Henry James   
2752   project_gutenberg/59462-0.txt  Henry James   
2835      project_gutenberg/8080.txt  Henry James   
3191      project_gutenberg/7813.txt  Henry James   
3645   project_gutenberg/58938-0.txt  Henry James   
3824      project_gutenberg/7529.txt  Henry James   
3991      project_gutenberg/7433.txt  Henry James   
4429   project_gutenberg/58471-0.txt  Henry James   
4542      project_gutenberg/7118.txt  Henry James   
5701       project_gutenberg/645.txt  Henry James   
5751       project_gutenberg/643.txt  Henry James   
5776       project_gutenberg/642.txt  Henry James   
7916       project_gutenberg/432.txt  Henry James   
8513     project_gutenberg/38035.txt  Henry James   
8946      project_gutenberg/4264.txt  Henry James   
9227     project_gutenberg/42486.txt  Henry James   
9597     project_gutenberg/37424.txt  Henry James   
12022  project_gutenberg/38776-0.txt  Henry James   
13206    project_gutenberg/26115.txt  Henry James   
13886    project_gutenberg/25767.txt  Henry James   
13953   project_gutenberg/3145-0.txt  Henry James   
14572     project_gutenberg/2534.txt  Henry James   
14796     project_gutenberg/2834.txt  Henry James   
15352    project_gutenberg/33325.txt  Henry James   
15359    project_gutenberg/28004.txt  Henry James   
16049     project_gutenberg/2426.txt  Henry James   
16066     project_gutenberg/2425.txt  Henry James   
16161   project_gutenberg/2715-0.txt  Henry James   
17526    project_gutenberg/21969.txt  Henry James   
17528    project_gutenberg/21968.txt  Henry James   
17855    project_gutenberg/21773.txt  Henry James   
17858    project_gutenberg/21772.txt  Henry James   
17862    project_gutenberg/21770.txt  Henry James   
18759      project_gutenberg/211.txt  Henry James   
18934      project_gutenberg/210.txt  Henry James   
19090      project_gutenberg/179.txt  Henry James   
19134      project_gutenberg/208.txt  Henry James   

                                                   title  year      sttr  \
1548                            The Lesson of the Master  1888  0.655667   
1727                                      The Birthplace  1903  0.690143   
1801                                  Notes on Novelists  1914  0.746167   
2752   Index of the Project Gutenberg Works of Henry ...  1909  0.446250   
2835                               A  Passionate Pilgrim  1609  0.721273   
3191                                    Madame de Mauves  1874  0.706692   
3645                                       English Hours  1905  0.748455   
3824                                    The Reverberator  1888  0.626619   
3991                                     The Awkward Age  1898  0.616980   
4429                                   Partial Portraits  1888  0.707415   
4542                                    What Maisie Knew  2012  0.636333   
5701                            The Figure in the Carpet  1896  0.700200   
5751                               The Death of the Lion  2002  0.700200   
5776                               The Altar of the Dead  1895  0.684000   
7916                                     The Ambassadors  1903  0.655088   
8513                 The Letters of Henry James, Vol. II  1843  0.713984   
8946                                     The Golden Bowl  1904  0.681722   
9227                                      The Two Magics  1898  0.672536   
9597                                   Views and Reviews  2004  0.722524   
12022              The Letters of Henry James (volume I)  1843  0.723696   
13206                             A Small Boy and Others  1913  0.778026   
13886                                   Picture and Text  1893  0.717154   
13953                           The Author of Beltraffio  1884  0.680143   
14572                                   Eugene Pickering  1968  0.687143   
14796      

In [339]:
metrics_embedded = TSNE(n_components=3).fit_transform(df_scaled_subset)

df_TSNE = pd.concat([df.iloc[:, :4], 
                     pd.DataFrame(metrics_embedded, columns=['TSNE_1', 
                                                             'TSNE_2', 
                                                             'TSNE_3'])], axis=1)

In [428]:
f = go.Figure(data=go.Scatter3d(x=df_TSNE.TSNE_1, 
                                y=df_TSNE.TSNE_2,
                                z=df_TSNE.TSNE_3,
                                mode='markers',
                                marker=dict(size=2,
                                            color=df_TSNE['TSNE_3'], 
                                            colorscale='PRGn'),
                                text='<b>' + df_TSNE['title'] + '</b>'
                                     '<br>' + 
                                     '<br>' + df_TSNE['author'] + '<br>' +
                                      df['year'].astype('str'),
                                hovertemplate='%{text}'
                               ))

f.update_layout(title='Stylometric Analysis of Project Gutenberg',
                height=1100,
                width=1100,
                template='plotly_white')
f.show()

0        1822
1        1941
2        1972
3        1970
4        2013
         ... 
19171    1810
19172    1860
19173    1952
19174    1934
19175    1215
Name: year, Length: 19176, dtype: object